# Introduction

- Projet final présenté par: **François Pelletier**
- Matricule: **908144032**
- Dans le cadre du cours: **IFT-7025**

# Librairies utilisées

In [ ]:
import numpy as np
import load_datasets as ld
import matplotlib.pyplot as plt
import DecisionTree
import NeuralNet

## Iris Dataset

La présentation des résultats liés à ce jeu de données servira aussi à expliquer les concepts et répondre aux questions. Pour les autres jeux de données, seul les résultats et la discussion seront détaillés.

- Chargement du jeu de données

In [ ]:
train1, train_labels1, test1, test_labels1 = (
    ld.load_iris_dataset(train_ratio = 0.7))

### Entrainement de l'arbre de décision

Dans cette section, on entraine un arbre de décision basé sur la mesure d'entropie.

In [ ]:
dt1 = DecisionTree.DecisionTree(attribute_type="continuous")
_ = dt1.train(train1, train_labels1,verbose=False)

### Courbe d'apprentissage

Je trace une courbe d'apprentissage qui effectue une validation croisée sur 10 sous-ensembles de l'ensemble d'entrainement. Je vais la moyenne de l'accuracy pour chaque sous-ensemble de test, puis j'itère en ajoutant un exemple à la fois à l'ensemble d'entrainement.

- Bogue connu: J'ai débuté à courbe d'apprentissage avec 30 données car j'ai de la difficulté à exécuter la validation croisée avec moins sans que ça plante vu que je crée les sous-groupes à l'avance.

In [ ]:
accuracy_cum = []
range_lc = range(30,len(train_labels1))
for i in range_lc:
    range_lc_split_test = np.array_split(range(i),10)
    range_lc_split_train = (
        [np.setdiff1d(range(i),t) for t in range_lc_split_test])
    accuracy_cv = []
    for r_i in range(10):
        try:
            training = dt1.train(train1[range_lc_split_train[r_i]], 
                                 train_labels1[range_lc_split_train[r_i]],
                                 verbose=False)
            test = dt1.test(train1[range_lc_split_test[r_i]], 
                            train_labels1[range_lc_split_test[r_i]],
                            verbose=False)
            accuracy_cv.append(test[1])
        except:
            pass
    accuracy_cum.append(np.mean(accuracy_cv))

Voici le graphique de la courbe d'apprentissage

In [ ]:
plt.plot(range_lc,accuracy_cum)

### Test et évaluation de la performance de l'arbre de décision

In [ ]:
_ = dt1.test(test1, test_labels1)

### Choix du nombre de neurones dans la couche cachée

On doit identifier le nombre optimal de neurones dans la couche cachée dans l'intervalle $[4,50]$ pour chacun des 5 jeux de données. On itère sur chacun des jeux de validation croisée, pour chaque dimension et on calcule l'accuracy moyenne. La dimension qui a la meilleure accuracy moyenne est choisie pour construire le réseau de neurones.

In [ ]:
choix_n_neurones = range(4,51)

- Pour faire la séparation du jeu de données en $k_{cv}=5$ jeux de validation croisée, on génère une permutation sur les indices du jeu d'entrainement, puis, on sépare cet ensemble en 5 groupes.

In [ ]:
k_cv = 5
all_indices = range(len(train_labels1))
np.random.seed(12345)
indices_cv_test = (
    np.sort(np.array_split(np.random.permutation(all_indices),
                           k_cv)))

In [ ]:
indices_cv_train = (
    [np.setdiff1d(all_indices,indices_cv_test[i]) for i in range(k_cv)])

Ce jeux de données a trois classes possibles comme variable de sortie. On utilisera donc un réseau de neurones avec 3 neurones dans la couche de sortie, une pour chacune des valeurs possibles. Les valeurs de sortie du jeu de données sont transformées à l'aide d'un encodage binaire où la valeur de sortie est convertie en rang dans un vecteur (on commence à 0), prenant la valeur 1. Par exemple, la valeur 2 devient $[0,0,1]$.

In [ ]:
accuracy_cum = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        nn1 = NeuralNet.NeuralNet(np.array([4,n_neurones,3]),range(3))
        nn1.train(train1[indices_cv_train[cv_set]], 
                  train_labels1[indices_cv_train[cv_set]], 0.1, 1, 
                  verbose=False)
        _,accuracy,_,_,_ = nn1.test(train1[indices_cv_test[cv_set]], 
                                    train_labels1[indices_cv_test[cv_set]], 
                                    verbose=False)
        accuracy_cv.append(accuracy)
    accuracy_cum.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal1 = (
    choix_n_neurones[np.where(accuracy_cum==max(accuracy_cum))[0][0]])
n_neurones_optimal1

### Choix du nombre de couches cachées

On choisit un nombre de 1 à 5 couches cachées. Le nombre de couche ayany l'accuracy maximale sera sélectionné pour la construction du réseau. On effectue 10 époques étant donné la taille des réseaux à entrainer.

In [ ]:
choix_n_couches = range(1,6)

In [ ]:
accuracy_cum = []
lc_cum = []
for n_couches in choix_n_couches:
    accuracy_cv=[]
    nn1 = NeuralNet.NeuralNet(
        np.hstack((4,
                   np.repeat(n_neurones_optimal1,n_couches),
                   3)),
        range(3))
    lc = nn1.train(train1, train_labels1, 0.1, 10, verbose=False)
    lc_cum.append(lc)
    _,accuracy,_,_,_ = nn1.test(train1, train_labels1, verbose=False)
    accuracy_cv.append(accuracy)
    accuracy_cum.append(np.mean(np.array(accuracy_cv)))
lc_cum = np.array(lc_cum)

L'accuracy pour les différentes profondeur est de :

In [ ]:
np.vstack((choix_n_couches,accuracy_cum))

Le nombre de couches cachées qui maximise l'accurary est de:

In [ ]:
n_couches_optimal1 = choix_n_couches[np.where(accuracy_cum==max(accuracy_cum))[0][0]]
n_couches_optimal1

Un problème rencontré avec un nombre de couches élevées est appelé le *Vanishing gradient problem*. Dans ces situaitons, le nombre de multiplications nécessaires ainsi que le fait que les valeurs $\Delta$ sont suffisamment petites pour que le gradient tende vers 0 et ainsi ne permette pas de mettre les poids à jour. Dans ces situations, l'entrainement va stagner.

### Courbes d'apprentissage

Ce graphique présente les courbes d'apprentissage pour chacun des niveaux de profondeur du réseau

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

### Choix des poids initiaux
Les poids initiaux ont été choisis à partir d'une distribution uniforme sur $[-1,1]$. On compare ici les courbes d'apprentissage en initialisant les poids à 0 et en initialisant les poids aléatoirement, pour le réseau de dimension et de profondeur optimale sélectionnées précédemment.

- Réseau initialisé avec les poids à 0 $RN_{0}$

In [ ]:
nn1_poidszero = NeuralNet.NeuralNet(
    np.hstack((4,
               np.repeat(n_neurones_optimal1,n_couches_optimal1),
               3)),
    range(3),
    input_weights=0)
lc_nn1_poidszero = (
    nn1_poidszero.train(train1, train_labels1, 0.1, 10, verbose=False))

- Réseau initialisé avec les poids uniformes $RN_{\neg{0}}$

In [ ]:
nn1_poidsunif = NeuralNet.NeuralNet(
    np.hstack((4,
               np.repeat(n_neurones_optimal1,n_couches_optimal1),
               3)),
    range(3))
np.random.seed(12345)
lc_nn1_poidsunif = (
    nn1_poidsunif.train(train1, train_labels1, 0.1, 10, verbose=False))

- Graphique des courbes d'apprentissage

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn1_poidszero, label="RN_Zero")
plt.plot(range(10),lc_nn1_poidsunif, label="RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

On remarque clairement que l'initialisation des poids à 0 ne permet pas de démarrer l'entrainement du réseau. Il est donc nécessaire d'initialiser les poids aléatoirement pour permettre l'apprentissage et éviter que les différentes fonctions pour calculer la rétropropagation des erreurs aient toutes des valeurs de 0.

### Entrainement et tests
On reprend les résultats du dernier entrainement, puisqu'il utilise les poids aléatoires et les hyperparamètres optimaux.

In [ ]:
_ = nn1_poidsunif.test(test1, test_labels1)